# **Ciência de Dados - IFSP Campinas**
# Trabalho Interdisciplinar - 2s2021 - D2APR/D2TEC

**Created by:**<br>
Rodrigo Barros ([@rpbarros](https://github.com/rpbarros)) - CP3013502 <br>
Vinicius Albano ([@vinialbano](https://github.com/vinialbano)) - CP3013677

<a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/4.0/"><img alt="Creative Commons License" style="border-width:0" src="https://i.creativecommons.org/l/by-nc-sa/4.0/88x31.png" /></a><br />This work is licensed under a <a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/4.0/">Creative Commons Attribution-NonCommercial-ShareAlike 4.0 International License</a>.

<h2 align="center">Flights in Brazil</h2>
<h2 align="center">A study on brazilian flights dataset for 2016/2017</h2>
<h3 align="center">Predict best flight choices</h3>
<img src="./images/airplane.jpg">

---



## 0. Imports and default settings for plotting

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib import ticker
import seaborn as sns
import plotly.offline as pyo
#!pip install chart_studio
#import chart_studio.plotly as py
from sklearn import metrics 
import plotly.graph_objects as go
#!pip install geopandas
#import geopandas as gpd
import warnings

import datetime as dt

warnings.filterwarnings('ignore')
pd.options.display.max_columns = 50

pd.set_option("display.max_rows", 150)

sns.set_theme(style="whitegrid")

params = {'legend.fontsize': 'x-large',
          'figure.figsize': (15, 5),
          'axes.labelsize': 'x-large',
          'axes.titlesize':'x-large',
          'xtick.labelsize':'x-large',
          'ytick.labelsize':'x-large'}
plt.rcParams.update(params)

%matplotlib inline

## 🔲 1. Frame the Problem

### 📄 1.1. Context

Brazil is the largest country in Latin America and the fifth-largest globally, with 8.5 million square kilometers (3,300,000 sq mi). The distance between the two extreme points from the north (Uiramutã - RR) to the south (Santa Vitória do Palmar - RS) is 4,394 km and from the two extremes from the east (João Pessoa - PB) to the west (Mâncio Lima - AC) is 4,319 km. The federation is formed by 26 states and the Federal District, where the capital (Brasília) is located.

To cover this entire continental dimension, the country has around 2,500 airports, including airfields – the second largest number in the world, after the United States. São Paulo-Guarulhos International Airport, near São Paulo, is the country's largest and busiest airport, handling nearly 20 million passengers annually and most of the country's commercial traffic.

As one of the largest emerging countries, the Brazilian civil aircraft fleet is one of the largest in the world, with more than 10,000 units flying. The country has fifteen active airlines nowadays. With these vast numbers, understanding the civil aircraft market seems important. 

This study aims to objectively analyze commercial aircraft routes, their operating companies, including origin/destination airports, delays, and cancellations. Thus, we will be able to better understand the Brazilian aircraft market, its operators, and routes.


**References:** <br/>
[Airlines of Brazil - Wikipedia](https://en.wikipedia.org/wiki/List_of_airlines_of_Brazil)<br/>
[ANAC - Wikipedia](https://en.wikipedia.org/wiki/National_Civil_Aviation_Agency_of_Brazil)<br/>
[Brazil - Wikipedia](https://en.wikipedia.org/wiki/Brazil)<br/>


### 🧠 1.2. Challenge

#### 🎯 **Objective:**
**Use machine learning to create a model that predicts flight delays in the Brazilian market.** <br/>

#### **Solution Planning:**
- **Classification problem**
- Metrics:
    - Accuracy
    - Precision
    - Recall
    - F1 Score
    - ROC Curve
    - AUC
- Data sources:
    - [Flights in Brazil](https://www.kaggle.com/ramirobentes/flights-in-brazil)
- No assumptions
- Project deliverable:
    - A simple exploratory data analysis
    - **A ML system/model** launched in _production_ <br/><br/>

## 💽 2. Get the Data

The considered dataset contains information of 2,5 million flights registered by the National Civil Aviation Agency of Brazil. Each register contains 21 features describing that specific flight, including Source/Destinaton airports, Delays, Geo Location, etc.
This dataset does not have legal obligations and sensitive information.

### 2.1. Download the Data

Flights in Brazil dataset is available at this [Kaggle repository](https://www.kaggle.com/ramirobentes/flights-in-brazil).

### 2.2. Load the Data

In [2]:
import zipfile
with zipfile.ZipFile('./datasets/BrFlights2.zip', 'r') as zip_ref:
    zip_ref.extractall('./datasets/')

In [3]:
df_full = pd.read_csv('./datasets/BrFlights2.csv', encoding="latin1")
df_full.head()

Voos        Companhia.Aerea Codigo.Tipo.Linha      Partida.Prevista  \
0  AAL - 203  AMERICAN AIRLINES INC     Internacional  2016-01-30T08:58:00Z   
1  AAL - 203  AMERICAN AIRLINES INC     Internacional  2016-01-13T12:13:00Z   
2  AAL - 203  AMERICAN AIRLINES INC     Internacional  2016-01-29T12:13:00Z   
3  AAL - 203  AMERICAN AIRLINES INC     Internacional  2016-01-19T12:13:00Z   
4  AAL - 203  AMERICAN AIRLINES INC     Internacional  2016-01-30T12:13:00Z   

           Partida.Real      Chegada.Prevista          Chegada.Real  \
0  2016-01-30T08:58:00Z  2016-01-30T10:35:00Z  2016-01-30T10:35:00Z   
1  2016-01-13T12:13:00Z  2016-01-13T21:30:00Z  2016-01-13T21:30:00Z   
2  2016-01-29T12:13:00Z  2016-01-29T21:30:00Z  2016-01-29T21:30:00Z   
3  2016-01-18T12:03:00Z  2016-01-19T21:30:00Z  2016-01-18T20:41:00Z   
4  2016-01-30T12:13:00Z  2016-01-30T21:30:00Z  2016-01-30T21:30:00Z   

  Situacao.Voo                       Codigo.Justificativa Aeroporto.Origem  \
0    Realizado                                        NaN      Afonso Pena   
1    Realizado                                        NaN    Salgado Filho   
2    Realizado                                        NaN    Salgado Filho   
3    Realizado  LIBERACAO SERV. TRAFEGO AEREO/ANTECIPACAO    Salgado Filho   
4    Realizado                                        NaN    Salgado Filho   

          Cidade.Origem Estado.Origem Pais.Origem Aeroporto.Destino  \
0  Sao Jose Dos Pinhais            PR      Brasil     Salgado Filho   
1          Porto Alegre            RS      Brasil             Miami   
2          Porto Alegre            RS      Brasil             Miami   
3          Porto Alegre            RS      Brasil             Miami   
4          Porto Alegre            RS      Brasil             Miami   

  Cidade.Destino Estado.Destino    Pais.Destino   LongDest    LatDest  \
0   Porto Alegre             RS          Brasil -51.175381 -29.993473   
1          Miami            N/I  Estados Unidos -80.287046  25.795865   
2          Miami            N/I  Estados Unidos -80.287046  25.795865   
3          Miami            N/I  Estados Unidos -80.287046  25.795865   
4          Miami            N/I  Estados Unidos -80.287046  25.795865   

    LongOrig    LatOrig  
0 -49.172481 -25.532713  
1 -51.175381 -29.993473  
2 -51.175381 -29.993473  
3 -51.175381 -29.993473  
4 -51.175381 -29.993473

In [4]:
#translate feature names to english
df_full.columns = ['flight_no', 'airline_company', 'route_type', 'departure_schedule', 'departure_actual', 
                       'arrival_schedule', 'arrival_actual', 'flight_status', 'just_code', 'airport_orig', 'city_orig', 
                       'state_orig', 'country_orig', 'airport_dest', 'city_dest', 'state_dest', 'country_dest',
                       'lon_dest', 'lat_dest', 'lon_orig', 'lat_orig']

df_full.head()

flight_no        airline_company     route_type    departure_schedule  \
0  AAL - 203  AMERICAN AIRLINES INC  Internacional  2016-01-30T08:58:00Z   
1  AAL - 203  AMERICAN AIRLINES INC  Internacional  2016-01-13T12:13:00Z   
2  AAL - 203  AMERICAN AIRLINES INC  Internacional  2016-01-29T12:13:00Z   
3  AAL - 203  AMERICAN AIRLINES INC  Internacional  2016-01-19T12:13:00Z   
4  AAL - 203  AMERICAN AIRLINES INC  Internacional  2016-01-30T12:13:00Z   

       departure_actual      arrival_schedule        arrival_actual  \
0  2016-01-30T08:58:00Z  2016-01-30T10:35:00Z  2016-01-30T10:35:00Z   
1  2016-01-13T12:13:00Z  2016-01-13T21:30:00Z  2016-01-13T21:30:00Z   
2  2016-01-29T12:13:00Z  2016-01-29T21:30:00Z  2016-01-29T21:30:00Z   
3  2016-01-18T12:03:00Z  2016-01-19T21:30:00Z  2016-01-18T20:41:00Z   
4  2016-01-30T12:13:00Z  2016-01-30T21:30:00Z  2016-01-30T21:30:00Z   

  flight_status                                  just_code   airport_orig  \
0     Realizado                                        NaN    Afonso Pena   
1     Realizado                                        NaN  Salgado Filho   
2     Realizado                                        NaN  Salgado Filho   
3     Realizado  LIBERACAO SERV. TRAFEGO AEREO/ANTECIPACAO  Salgado Filho   
4     Realizado                                        NaN  Salgado Filho   

              city_orig state_orig country_orig   airport_dest     city_dest  \
0  Sao Jose Dos Pinhais         PR       Brasil  Salgado Filho  Porto Alegre   
1          Porto Alegre         RS       Brasil          Miami         Miami   
2          Porto Alegre         RS       Brasil          Miami         Miami   
3          Porto Alegre         RS       Brasil          Miami         Miami   
4          Porto Alegre         RS       Brasil          Miami         Miami   

  state_dest    country_dest   lon_dest   lat_dest   lon_orig   lat_orig  
0         RS          Brasil -51.175381 -29.993473 -49.172481 -25.532713  
1        N/I  Estados Unidos -80.287046  25.795865 -51.175381 -29.993473  
2        N/I  Estados Unidos -80.287046  25.795865 -51.175381 -29.993473  
3        N/I  Estados Unidos -80.287046  25.795865 -51.175381 -29.993473  
4        N/I  Estados Unidos -80.287046  25.795865 -51.175381 -29.993473

### 2.3. Take a quick look at the data structure

In [5]:
df_full.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542519 entries, 0 to 2542518
Data columns (total 21 columns):
 #   Column              Dtype  
---  ------              -----  
 0   flight_no           object 
 1   airline_company     object 
 2   route_type          object 
 3   departure_schedule  object 
 4   departure_actual    object 
 5   arrival_schedule    object 
 6   arrival_actual      object 
 7   flight_status       object 
 8   just_code           object 
 9   airport_orig        object 
 10  city_orig           object 
 11  state_orig          object 
 12  country_orig        object 
 13  airport_dest        object 
 14  city_dest           object 
 15  state_dest          object 
 16  country_dest        object 
 17  lon_dest            float64
 18  lat_dest            float64
 19  lon_orig            float64
 20  lat_orig            float64
dtypes: float64(4), object(17)
memory usage: 407.4+ MB


In [6]:
# fixing the data types
df_full['airline_company'] = df_full['airline_company'].astype('category')
df_full['flight_no'] = df_full['flight_no'].astype('category')
df_full['route_type'] = df_full['route_type'].astype('category')
df_full['departure_schedule'] = pd.to_datetime(df_full['departure_schedule'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_full['departure_actual'] = pd.to_datetime(df_full['departure_actual'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_full['arrival_schedule'] = pd.to_datetime(df_full['arrival_schedule'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_full['arrival_actual'] = pd.to_datetime(df_full['arrival_actual'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_full['flight_status'] = df_full['flight_status'].astype('category')
df_full['just_code'] = df_full['just_code'].astype('category')
df_full['airport_orig'] = df_full['airport_orig'].astype('category')
df_full['airport_dest'] = df_full['airport_dest'].astype('category')
df_full['city_orig'] = df_full['city_orig'].astype('category')
df_full['city_dest'] = df_full['city_dest'].astype('category')
df_full['state_orig'] = df_full['state_orig'].astype('category')
df_full['state_dest'] = df_full['state_dest'].astype('category')
df_full['country_orig'] = df_full['country_orig'].astype('category')
df_full['country_dest'] = df_full['country_dest'].astype('category')

In [7]:
df_full.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542519 entries, 0 to 2542518
Data columns (total 21 columns):
 #   Column              Dtype         
---  ------              -----         
 0   flight_no           category      
 1   airline_company     category      
 2   route_type          category      
 3   departure_schedule  datetime64[ns]
 4   departure_actual    datetime64[ns]
 5   arrival_schedule    datetime64[ns]
 6   arrival_actual      datetime64[ns]
 7   flight_status       category      
 8   just_code           category      
 9   airport_orig        category      
 10  city_orig           category      
 11  state_orig          category      
 12  country_orig        category      
 13  airport_dest        category      
 14  city_dest           category      
 15  state_dest          category      
 16  country_dest        category      
 17  lon_dest            float64       
 18  lat_dest            float64       
 19  lon_orig            float64       
 20  la

### 2.4. Features description

Each row corresponds to a flight registered by ANAC in 2016/2017 years.

Each flight is represented by **21 features** (4 numeric and 13 categorical and 4 date time).

<table style="border-collapse: collapse;font-size: 14px; width:800px;">
  <tr>
    <th style="background-color:#D3DBDD;text-align:left">Feature</th>
    <th style="width:500px; background-color:#D3DBDD;text-align:center">Description</th>
    <th style="background-color:#D3DBDD;">Type</th>
  </tr>
  <tr>
    <td style="text-align:left">flight_no</td>
    <td style="text-align:center">Flight identification code</td>
    <td>Categorical</td>
  </tr>    
  <tr>
    <td style="text-align:left">airline_company</td>
    <td style="text-align:center">Name of the airline company</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">route_type </td>
    <td style="text-align:center">Type of the Route: Internacional, Regional, Nacional</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">departure_schedule</td>
    <td style="text-align:center">Date and time scheduled for the flight departure</td>
    <td>DateTime</td>
  </tr>
  <tr>
    <td style="text-align:left">departure_actual </td>
    <td style="text-align:center">Actual date and time of the flight departure</td>
    <td>DateTime</td>
  </tr>
  <tr>
    <td style="text-align:left">arrival_schedule </td>
    <td style="text-align:center">Date and time scheduled for the flight arrival</td>
    <td>DateTime</td>
  </tr>
  <tr>
    <td style="text-align:left">arrival_actual </td>
    <td style="text-align:center">Actual date and time of the flight arrival</td>
    <td>DateTime</td>
  </tr>
  <tr>
    <td style="text-align:left">flight_status</td>
    <td style="text-align:center">Flight status: Realizado, Cancelado</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">just_code</td>
    <td style="text-align:center">Explanation for any inconvenience on the flight.</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">airport_orig</td>
    <td style="text-align:center">Origin Airports name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">city_orig</td>
    <td style="text-align:center">Origin Cities name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">state_orig</td>
    <td style="text-align:center">Origin Country state, information valid for flights originated on Brazilian cities</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">country_orig</td>
    <td style="text-align:center">Origin Countries Name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">airport_dest</td>
    <td style="text-align:center">Destination Airports Name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">city_dest</td>
    <td style="text-align:center">Destination Cities name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">state_dest</td>
    <td style="text-align:center">Destination Country state, information valid for flights destinated to Brazilian cities</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">country_dest</td>
    <td style="text-align:center">Destination Countries Name</td>
    <td>Categorical</td>
  </tr>
  <tr>
    <td style="text-align:left">lon_dest</td>
    <td style="text-align:center">Destination´s longitude coordinate</td>
    <td>Numeric</td>
  </tr>
  <tr>
    <td style="text-align:left">lat_dest</td>
    <td style="text-align:center">Destination´s latitude coordinate</td>
    <td>Numeric</td>
  </tr>  
  <tr>
    <td style="text-align:left">lon_orig</td>
    <td style="text-align:center">Origin´s longitude coordinate</td>
    <td>Numeric</td>
  </tr>
  <tr>
    <td style="text-align:left">lat_orig</td>
    <td style="text-align:center">Origin´s latitude coordinate</td>
    <td>Numeric</td>
  </tr>    
</table>

### 2.5. Inspect for missing data

In [8]:
df_full.isnull().sum()

flight_no                   0
airline_company             0
route_type                  0
departure_schedule          0
departure_actual       289196
arrival_schedule            0
arrival_actual         289196
flight_status               0
just_code             1510212
airport_orig                0
city_orig                   0
state_orig                  0
country_orig                0
airport_dest                0
city_dest                   0
state_dest                  0
country_dest                0
lon_dest                    0
lat_dest                    0
lon_orig                    0
lat_orig                    0
dtype: int64

It seems we have an equal number of missing values for departure and arrival actual datetime. This is possible to be related to cancelled flights.

To confirm this information, a comparision with the number of cancelled flights can be easily done:

In [9]:
index = df_full.loc[df_full['flight_status'] == 'Cancelado'].index
len(index)

289196

Indeed, the number of cancelled flights is exactly the same as the number of missing departure/arrival actual datetime.

The other field that contains missing values is the Justification Code of a flight, which possibly will not be relevant for a flight that departed and arrived on time. This can also be checked.

In [10]:
index = df_full.loc[(df_full['departure_schedule'] != df_full['departure_actual']) | (df_full['arrival_schedule'] != df_full['arrival_actual'])].index
len(index)

1053799

The number of flights with departure and arrival is not the same as expected, since it doesn't match the number of Justifications.

In [12]:
unmatch = df_full.loc[(df_full['departure_schedule'] == df_full['departure_actual']) & (df_full['arrival_schedule'] == df_full['arrival_actual']) & (df_full['just_code'] == df_full['just_code'])]
unmatch['just_code'].unique()

['ATRASOS NAO ESPECIFICOS - OUTROS', 'TROCA DE AERONAVE', 'AEROPORTO COM RESTRICOES OPERACIONAIS', 'AEROPORTO DESTINO ABAIXO DOS LIMITES', 'CONEXAO AERONAVE/VOLTA - VOO DE IDA NAO PENAL..., ..., 'CONEXAO DE AERONAVE', 'AVARIA DURANTE OPERACOES EM VOO', 'AEROPORTO ORIGEM ABAIXO DOS LIMITES', 'ANTECIPACAO DE HORARIO AUTORIZADA - ESPECIFIC..., 'AEROPORTO DE DESTINO INTERDITADO']
Length: 16
Categories (16, object): ['ATRASOS NAO ESPECIFICOS - OUTROS', 'TROCA DE AERONAVE', 'AEROPORTO COM RESTRICOES OPERACIONAIS', 'AEROPORTO DESTINO ABAIXO DOS LIMITES', ..., 'AVARIA DURANTE OPERACOES EM VOO', 'AEROPORTO ORIGEM ABAIXO DOS LIMITES', 'ANTECIPACAO DE HORARIO AUTORIZADA - ESPECIFIC..., 'AEROPORTO DE DESTINO INTERDITADO']

Apparently, even though a flight is on time, for some reason the Justification field still apply. This may be related to a number of reasons, like a reschedule of a previous delayed flight. 

Given that, the dataset seems to hold integrity and no additional data fix is needed.

## 3. Data Cleaning

In [13]:
df_full.columns

Index(['flight_no', 'airline_company', 'route_type', 'departure_schedule',
       'departure_actual', 'arrival_schedule', 'arrival_actual',
       'flight_status', 'just_code', 'airport_orig', 'city_orig', 'state_orig',
       'country_orig', 'airport_dest', 'city_dest', 'state_dest',
       'country_dest', 'lon_dest', 'lat_dest', 'lon_orig', 'lat_orig'],
      dtype='object')

The first thing we can see here is that there are multiple types of information into a single table:
* **Flights**, with their code, airline company and type
* **Trips** information like the times of departure and arrival, status, and justification.
* **Airports** and their locations.

We can split our dataset into 3 separate tables.

### 3.1 Creating the Airports dataset

In [14]:
airports_orig_cols = ['airport_dest', 'city_dest', 'state_dest',
       'country_dest', 'lon_dest', 'lat_dest']

airports_dest_cols = ['airport_orig', 'city_orig', 'state_orig',
       'country_orig', 'lon_orig', 'lat_orig']

airports_cols = ['airport', 'city', 'state', 'country', 'longitude', 'latitude']

In [15]:
df_airports_orig = df_full[airports_orig_cols].drop_duplicates()
df_airports_orig.columns = airports_cols

In [16]:
df_airports_dest = df_full[airports_dest_cols].drop_duplicates()
df_airports_dest.columns = airports_cols

In [17]:
df_airports = df_airports_orig.append(df_airports_dest, ignore_index=True).drop_duplicates().reset_index(drop=True)
df_airports["airport_id"] = df_airports.index
df_airports.head(10)

airport                  city  \
0                                     Salgado Filho          Porto Alegre   
1                                             Miami                 Miami   
2                                       Afonso Pena  Sao Jose Dos Pinhais   
3                   Presidente Juscelino Kubitschek              Brasilia   
4                   Deputado Luis Eduardo Magalhaes              Salvador   
5       Guarulhos - Governador Andre Franco Montoro             Guarulhos   
6                      Guararapes - Gilberto Freyre                Recife   
7  Aeroporto Internacional Do Rio De Janeiro/Galeao        Rio De Janeiro   
8                                         Viracopos              Campinas   
9                                          New York              New York   

  state         country  longitude   latitude  airport_id  
0    RS          Brasil -51.175381 -29.993473           0  
1   N/I  Estados Unidos -80.287046  25.795865           1  
2    PR          Brasil -49.172481 -25.532713           2  
3    DF          Brasil -47.917235 -15.869737           3  
4    BA          Brasil -38.331241 -12.911098           4  
5    SP          Brasil -46.478126 -23.434553           5  
6    PE          Brasil -34.924015  -8.125932           6  
7    RJ          Brasil -43.249423 -22.813410           7  
8    SP          Brasil -47.137569 -23.008205           8  
9   N/I  Estados Unidos -73.778139  40.641311           9

In [18]:
df_airports.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 191 entries, 0 to 190
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   airport     191 non-null    object  
 1   city        191 non-null    object  
 2   state       191 non-null    category
 3   country     191 non-null    object  
 4   longitude   191 non-null    float64 
 5   latitude    191 non-null    float64 
 6   airport_id  191 non-null    int64   
dtypes: category(1), float64(2), int64(1), object(3)
memory usage: 10.7+ KB


In [19]:
# fixing the data types
df_airports['airport'] = df_airports['airport'].astype('category')
df_airports['city'] = df_airports['city'].astype('category')
df_airports['state'] = df_airports['state'].astype('category')
df_airports['country'] = df_airports['country'].astype('category')

### 3.1.1 Airports with routes to Brazilian cities

In [ ]:
import plotly.graph_objects as go

import pandas as pd

fig = go.Figure(data=go.Scattergeo(
        lon = df_airports['longitude'],
        lat = df_airports['latitude'],
        text = df_airports['airport'] + ', ' + df_airports['country'],
        mode = 'markers',
        marker = dict(size = 5, color = 'blue'),
        ))

fig.update_layout(
        geo= dict(showland = True, landcolor = 'white', countrycolor = 'grey', bgcolor="lightgrey"),
    )
fig.show()

### 3.2. Creating the Flights dataset

In [20]:
flight_cols = ['flight_no', 'airline_company', 'route_type']
df_flights = df_full[flight_cols].drop_duplicates().reset_index(drop=True)

In [21]:
df_flights.sample(10)

flight_no                      airline_company     route_type
7557  TAM - 3175                                  TAM       Regional
8292   CMP - 313  COPA -COMPANIA PANAMENA DE AVIACION  Internacional
3231  ONE - 6243                       AVIANCA BRASIL       Nacional
3812  TAM - 3411                                  TAM       Nacional
7929  AZU - 6947                                 AZUL       Regional
2235  GLO - 1451                                  GOL       Nacional
3790  TAM - 3380                                  TAM       Regional
7214  GLO - 2131                                  GOL       Nacional
2032  GLO - 1233                                  GOL       Nacional
6242  GLO - 6839                                  GOL       Nacional

In [22]:
df_flights.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8882 entries, 0 to 8881
Data columns (total 3 columns):
 #   Column           Non-Null Count  Dtype   
---  ------           --------------  -----   
 0   flight_no        8882 non-null   category
 1   airline_company  8882 non-null   category
 2   route_type       8882 non-null   category
dtypes: category(3)
memory usage: 246.7 KB


In [23]:
# fixing the data types
df_flights['airline_company'] = df_flights['airline_company'].astype('category')
df_flights['flight_no'] = df_flights['flight_no'].astype('category')
df_flights['route_type'] = df_flights['route_type'].astype('category')

### 3.3. Creating the Trips dataset

In [24]:
# appending the origin airport_id
df_trips = pd.merge(df_full, df_airports, left_on=airports_orig_cols,
                   right_on=airports_cols, how='left')
df_trips.drop(columns=airports_cols, inplace=True)

In [25]:
# appending the destination airport_id
df_trips = pd.merge(df_trips, df_airports, left_on=airports_dest_cols,
                   right_on=airports_cols, 
                   suffixes=('_origin', '_destination'),
                     how='left')
df_trips.drop(columns=airports_cols, inplace=True)

In [26]:
# removing the origin, destination, and flight specific columns
df_trips.drop(columns=airports_orig_cols, inplace=True)
df_trips.drop(columns=airports_dest_cols, inplace=True)
df_trips.drop(columns=['airline_company', 'route_type'], inplace=True)

In [27]:
df_trips.sample(10)

flight_no  departure_schedule    departure_actual  \
1754084  AZU - 4951 2015-04-09 16:35:00 2015-04-09 16:21:00   
938810   AZU - 2611 2017-01-28 15:15:00 2017-01-28 15:10:00   
102193   AZU - 4047 2016-02-09 19:47:00 2016-02-09 19:36:00   
597575   GLO - 7642 2016-08-24 22:40:00 2016-08-24 22:40:00   
1352043  ONE - 6142 2017-06-16 14:18:00 2017-06-16 14:18:00   
1794378  AZU - 4118 2015-04-02 18:41:00 2015-04-02 18:41:00   
556461   TAM - 3737 2016-07-11 05:45:00 2016-07-11 05:45:00   
1608670  TAM - 3264 2015-02-27 17:40:00 2015-02-27 17:40:00   
1445993  TAM - 3764 2017-07-21 20:33:00 2017-07-21 20:33:00   
2249977  TAM - 3558 2015-09-15 11:20:00 2015-09-15 11:20:00   

           arrival_schedule      arrival_actual flight_status  \
1754084 2015-04-09 17:59:00 2015-04-09 17:38:00     Realizado   
938810  2017-01-28 16:30:00 2017-01-28 16:22:00     Realizado   
102193  2016-02-09 21:05:00 2016-02-09 20:48:00     Realizado   
597575  2016-08-25 00:50:00 2016-08-25 00:50:00     Realizado   
1352043 2017-06-16 15:36:00 2017-06-16 15:36:00     Realizado   
1794378 2015-04-02 20:02:00 2015-04-02 20:02:00     Realizado   
556461  2016-07-11 06:45:00 2016-07-11 06:45:00     Realizado   
1608670 2015-02-27 18:53:00 2015-02-27 18:53:00     Realizado   
1445993 2017-07-21 21:40:00 2017-07-21 21:40:00     Realizado   
2249977 2015-09-15 13:15:00 2015-09-15 13:15:00     Realizado   

                                 just_code  airport_id_origin  \
1754084  ANTECIPACAO DE HORARIO AUTORIZADA                 11   
938810   ANTECIPACAO DE HORARIO AUTORIZADA                 25   
102193   ANTECIPACAO DE HORARIO AUTORIZADA                  8   
597575                                 NaN                123   
1352043                                NaN                  6   
1794378                                NaN                  8   
556461                                 NaN                 33   
1608670                                NaN                 11   
1445993                                NaN                 33   
2249977                                NaN                  5   

         airport_id_destination  
1754084                       3  
938810                       54  
102193                       11  
597575                        5  
1352043                       4  
1794378                      11  
556461                       68  
1608670                      33  
1445993                      35  
2249977                      40

In [28]:
df_trips.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2542519 entries, 0 to 2542518
Data columns (total 9 columns):
 #   Column                  Dtype         
---  ------                  -----         
 0   flight_no               category      
 1   departure_schedule      datetime64[ns]
 2   departure_actual        datetime64[ns]
 3   arrival_schedule        datetime64[ns]
 4   arrival_actual          datetime64[ns]
 5   flight_status           category      
 6   just_code               category      
 7   airport_id_origin       int64         
 8   airport_id_destination  int64         
dtypes: category(3), datetime64[ns](4), int64(2)
memory usage: 145.7 MB


In [29]:
# fixing the data types
df_trips['departure_schedule'] = pd.to_datetime(df_trips['departure_schedule'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_trips['departure_actual'] = pd.to_datetime(df_trips['departure_actual'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_trips['arrival_schedule'] = pd.to_datetime(df_trips['arrival_schedule'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_trips['arrival_actual'] = pd.to_datetime(df_trips['arrival_actual'], format = '%Y-%m-%dT%H:%M:%SZ', errors = 'coerce')
df_trips['flight_status'] = df_trips['flight_status'].astype('category')
df_trips['just_code'] = df_trips['just_code'].astype('category')
df_flights['flight_no'] = df_flights['flight_no'].astype('category')

### 3.4. Saving the new datasets

In [30]:
# write a pandas dataframes to zipped CSV files
df_flights.to_csv("./datasets/df_flights.zip", 
           index=False, 
           compression="zip")
df_airports.to_csv("./datasets/df_airports.zip", 
           index=False, 
           compression="zip")
df_trips.to_csv("./datasets/df_trips.zip", 
           index=False, 
           compression="zip")

In [31]:
# write a pandas dataframes to CSV files
df_flights.to_csv("./datasets/df_flights.csv", 
           index=False)
df_airports.to_csv("./datasets/df_airports.csv", 
           index=False)
df_trips.to_csv("./datasets/df_trips.csv", 
           index=False)

### 3.5 Tables Diagram
At the end, three tables are created, with the relationship between them stablished by foreign key on trips table for origin/destination airports and flights.
<img src="./images/tables.png">


## 4. Sagemaker + PySpark
With the knowledge gathered so far, it is also possible to explore ditributed computer techniques, as Sagemaker + PySpark offers on AWS environment.
This section is inspired by the tutorial ["Distributed Data Processing using Apache Spark and SageMaker Processing"](https://sagemaker-examples.readthedocs.io/en/latest/sagemaker_processing/spark_distributed_data_processing/sagemaker-spark-processing.html).

### 4.1 Architecture

<img src="./images/architecture.jpg">

### 4.2 Install the latest SageMaker Python SDK

In [32]:
!pip install -U sagemaker

     |████████████████████████████████| 466 kB 20.7 MB/s eta 0:00:01
     |████████████████████████████████| 131 kB 71.1 MB/s eta 0:00:01
     |████████████████████████████████| 8.4 MB 52.7 MB/s eta 0:00:01
  Created wheel for sagemaker: filename=sagemaker-2.70.0-py2.py3-none-any.whl size=649170 sha256=752efeaea4f8cc2812e7817d6a60f03864526de9d3f537422300507b3e33c390
  Stored in directory: /home/ec2-user/.cache/pip/wheels/da/11/20/c45ef599886a2b1399effa68f80b98b2166dc624e19636c303
Successfully built sagemaker
  Attempting uninstall: botocore
    Found existing installation: botocore 1.23.4
    Uninstalling botocore-1.23.4:
      Successfully uninstalled botocore-1.23.4
  Attempting uninstall: boto3
    Found existing installation: boto3 1.20.4
    Uninstalling boto3-1.20.4:
      Successfully uninstalled boto3-1.20.4
  Attempting uninstall: sagemaker
    Found existing installation: sagemaker 2.68.0
    Uninstalling sagemaker-2.68.0:
      Successfully uninstalled sagemaker-2.68.0
ERROR

### 4.3 Setup S3 bucket locations and roles

In [33]:
import logging
import sagemaker
from time import gmtime, strftime

sagemaker_logger = logging.getLogger("sagemaker")
sagemaker_logger.setLevel(logging.INFO)
sagemaker_logger.addHandler(logging.StreamHandler())

sagemaker_session = sagemaker.Session()
bucket = sagemaker_session.default_bucket()
role = sagemaker.get_execution_role()

### 4.4 Prepare the PySpark script

In [47]:
%%writefile ./code/preprocess.py
from __future__ import print_function
from __future__ import unicode_literals

import argparse
import csv
import os
import shutil
import sys
import time

import pyspark
# import sql function pyspark
import pyspark.sql.functions as f
from pyspark.sql import SparkSession
from pyspark.sql import SQLContext
from pyspark.ml import Pipeline
from pyspark.ml.feature import (
    OneHotEncoder,
    StringIndexer,
    VectorAssembler,
    VectorIndexer,
    Imputer,
)
from pyspark.sql.functions import *
from pyspark.sql.types import (
    DoubleType,
    StringType,
    DateType,
    StructField,
    StructType,
)


def csv_line(data):
    r = ",".join(str(d) for d in data[1])
    return str(data[0]) + "," + r

def main():
    parser = argparse.ArgumentParser(description="app inputs and outputs")
    parser.add_argument("--s3_input_bucket", type=str, help="s3 input bucket")
    parser.add_argument("--s3_input_key_prefix", type=str, help="s3 input key prefix")
    parser.add_argument("--s3_output_bucket", type=str, help="s3 output bucket")
    parser.add_argument("--s3_output_key_prefix", type=str, help="s3 output key prefix")
    args = parser.parse_args()

    spark = SparkSession.builder.appName("PySparkApp").getOrCreate()

    # This is needed to save RDDs which is the only way to write nested Dataframes into CSV format
    spark.sparkContext._jsc.hadoopConfiguration().set(
        "mapred.output.committer.class", "org.apache.hadoop.mapred.FileOutputCommitter"
    )
    
    # Defining the schema corresponding to the input data. This will also rename the columns to english.
    schema = StructType(
        [
            StructField("flight_no", StringType(), True),
            StructField("airline_company", StringType(), True),
            StructField("route_type", StringType(), True),
            StructField("departure_schedule", StringType(), True),
            StructField("departure_actual", StringType(), True),
            StructField("arrival_schedule", StringType(), True),
            StructField("arrival_actual", StringType(), True),
            StructField("flight_status", StringType(), True),
            StructField("just_code", StringType(), True),
            StructField("airport_orig", StringType(), True),
            StructField("city_orig", StringType(), True),
            StructField("state_orig", StringType(), True),
            StructField("country_orig", StringType(), True),
            StructField("airport_dest", StringType(), True),
            StructField("state_dest", StringType(), True),
            StructField("city_dest", StringType(), True),
            StructField("country_dest", StringType(), True),
            StructField("lon_dest", DoubleType(), True),
            StructField("lat_dest", DoubleType(), True),
            StructField("lon_orig", DoubleType(), True),
            StructField("lat_orig", DoubleType(), True),
        ]
    )

    # Downloading the data from S3 into a Dataframe
    total_df = spark.read.csv(
        ("s3://" + os.path.join(args.s3_input_bucket, args.s3_input_key_prefix, "BrFlights2.csv")),
        header=True,#ignore reader when loading DF.
        schema=schema,
    )
    
    # null values in each column
    data_agg = total_df.agg(*[f.count(f.when(f.isnull(c), c)).alias(c) for c in total_df.columns])
    data_agg.show()
    
    # StringIndexer on the flight_no column which has categorical value
    flight_no_indexer = StringIndexer(inputCol="flight_no", outputCol="indexed_flight_no", handleInvalid="skip")

    # The pipeline comprises of the step added above only
    pipeline = Pipeline(stages=[flight_no_indexer])

    # This step trains the feature transformer
    model = pipeline.fit(total_df)

    # This step transforms the dataset with information obtained from the previous fit
    transformed_total_df = model.transform(total_df)
    transformed_total_df.show(10)
    
    #Creates a temporary view of the DataFrame
    transformed_total_df.createOrReplaceTempView("total_df_table")
    transformed_total_df.cache()
    
    # all airports.
    airports_df_orig = spark.sql("SELECT airport_orig as airport, city_orig as city, state_orig as state, country_orig as country, lon_orig as longitude, lat_orig as latitude from total_df_table").dropDuplicates()

    #Creates a temporary view of the DataFrame
    transformed_total_df.createOrReplaceTempView("total_df_table")
    transformed_total_df.cache()
    
    airports_df_dest = spark.sql("SELECT airport_dest as airport, city_dest as city, state_dest as state, country_dest as country, lon_dest as longitude, lat_dest as latitude from total_df_table").dropDuplicates()
    airports_df = airports_df_orig.union(airports_df_dest).dropDuplicates()
    airports_df.show(10)

    # StringIndexer on the airport column which has categorical value
    airport_indexer = StringIndexer(inputCol="airport", outputCol="indexed_airport", handleInvalid="skip")

    # The pipeline comprises of the step added above only
    pipelineAirport = Pipeline(stages=[airport_indexer])  

    # This step trains the feature transformer
    modelAirport = pipelineAirport.fit(airports_df)

    # This step transforms the dataset with information obtained from the previous fit
    transformed_airports_df = modelAirport.transform(airports_df)
    transformed_airports_df.show(10)
   
    flights_df = spark.sql("SELECT indexed_flight_no, flight_no, airline_company, route_type from total_df_table").dropDuplicates()
    flights_df.show(10)
    
    #Creates a temporary view of the DataFrame
    transformed_airports_df.createOrReplaceTempView("airports_table")
    transformed_airports_df.cache()
    
    trips_df = spark.sql("SELECT indexed_flight_no, departure_schedule, departure_actual, arrival_schedule, arrival_actual, flight_status, just_code, airport_orig, airport_dest from total_df_table")
    trips_df.show(10)

    #Creates a temporary view of the DataFrame
    trips_df.createOrReplaceTempView("trips_table")
    trips_df.cache()
    
    trips_df = spark.sql("SELECT trips_table.indexed_flight_no, trips_table.departure_schedule, trips_table.departure_actual, trips_table.arrival_schedule, trips_table.arrival_actual, trips_table.flight_status, trips_table.just_code, airports_table.indexed_airport as indexed_airport_orig, trips_table.airport_dest from trips_table left join airports_table on trips_table.airport_orig = airports_table.airport")
    trips_df.show(10)

    #Creates a temporary view of the DataFrame
    trips_df.createOrReplaceTempView("trips_table")
    trips_df.cache()
    
    trips_df = spark.sql("SELECT trips_table.indexed_flight_no, trips_table.departure_schedule, trips_table.departure_actual, trips_table.arrival_schedule, trips_table.arrival_actual, trips_table.flight_status, trips_table.just_code, trips_table.indexed_airport_orig, airports_table.indexed_airport as indexed_airport_dest from trips_table left join airports_table on trips_table.airport_dest = airports_table.airport")
    trips_df.show(10)

    # Split the overall dataset into 80-20 training and validation
    (train_df, validation_df) = trips_df.randomSplit([0.8, 0.2])
    
    # Convert the train dataframe to RDD to save in CSV format and upload to S3
    #train_rdd = train_df.rdd.map(lambda x: (x.rings, x.features))
    #train_lines = train_rdd.map(csv_line)
    #train_lines.saveAsTextFile(
    #    "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "train")
    #)

    # Convert the validation dataframe to RDD to save in CSV format and upload to S3
    #validation_rdd = validation_df.rdd.map(lambda x: (x.rings, x.features))
    #validation_lines = validation_rdd.map(csv_line)
    #validation_lines.saveAsTextFile(
    #    "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "validation")
    #)
    
    train_df.write.csv(
        "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "train")
    )

    validation_df.write.csv(
        "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "validation")
    )
    
    airports_df.write.csv(
        "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "airport")
    )
    
    flights_df.write.csv(
        "s3://" + os.path.join(args.s3_output_bucket, args.s3_output_key_prefix, "flights")
    )


if __name__ == "__main__":
    main()

Overwriting ./code/preprocess.py


### 4.5 Run the SageMaker Processing Job

In [48]:
from sagemaker.spark.processing import PySparkProcessor

# Upload the raw input dataset to a unique S3 location
timestamp_prefix = strftime("%Y-%m-%d-%H-%M-%S", gmtime())
prefix = "sagemaker/spark-preprocess-flights/{}".format(timestamp_prefix)
input_prefix_flights = "{}/input/raw/flights".format(prefix)
input_preprocessed_prefix_flights = "{}/input/preprocessed/flights".format(prefix)

sagemaker_session.upload_data(
    path="./datasets/BrFlights2.csv", bucket=bucket, key_prefix=input_prefix_flights
)

# Run the processing job
spark_processor = PySparkProcessor(
    base_job_name="sm-spark",
    framework_version="2.4",
    role=role,
    instance_count=2,
    instance_type="ml.m5.xlarge",
    max_runtime_in_seconds=1200,
)

spark_processor.run(
    submit_app="./code/preprocess.py",
    arguments=[
        "--s3_input_bucket", bucket,
        "--s3_input_key_prefix", input_prefix_flights,
        "--s3_output_bucket", bucket,
        "--s3_output_key_prefix", input_preprocessed_prefix_flights,
    ],
    spark_event_logs_s3_uri="s3://{}/{}/spark_event_logs".format(bucket, prefix),
    logs=True,
)

Creating processing-job with name sm-spark-2021-12-06-04-53-34-443



Job Name:  sm-spark-2021-12-06-04-53-34-443
Inputs:  [{'InputName': 'code', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-us-east-1-193890026231/sm-spark-2021-12-06-04-53-34-443/input/code/preprocess.py', 'LocalPath': '/opt/ml/processing/input/code', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}]
Outputs:  [{'OutputName': 'output-1', 'AppManaged': False, 'S3Output': {'S3Uri': 's3://sagemaker-us-east-1-193890026231/sagemaker/spark-preprocess-flights/2021-12-06-04-53-28/spark_event_logs', 'LocalPath': '/opt/ml/processing/spark-events/', 'S3UploadMode': 'Continuous'}}]
...........................12-06 04:57 smspark.cli  INFO     Parsing arguments. argv: ['/usr/local/bin/smspark-submit', '--local-spark-event-logs-dir', '/opt/ml/processing/spark-events/', '/opt/ml/processing/input/code/preprocess.py', '--s3_input_bucket', 'sagemaker-us-east-1-193890026231', '--s3_input_key_prefix', 'sagemaker/spark-pr

In [49]:
!aws s3 ls s3://$bucket/$input_preprocessed_prefix_flights/train/ | head -n5

2021-12-06 04:59:43          0 _SUCCESS
2021-12-06 04:59:31   64215004 part-00000-1853362b-e8c2-4087-b5b4-30c05b6e59df-c000.csv
2021-12-06 04:59:34   64088207 part-00001-1853362b-e8c2-4087-b5b4-30c05b6e59df-c000.csv
2021-12-06 04:59:31   64512373 part-00002-1853362b-e8c2-4087-b5b4-30c05b6e59df-c000.csv
2021-12-06 04:59:34   64231402 part-00003-1853362b-e8c2-4087-b5b4-30c05b6e59df-c000.csv

[Errno 32] Broken pipe
Exception ignored in: <_io.TextIOWrapper name='<stdout>' mode='w' encoding='UTF-8'>
BrokenPipeError: [Errno 32] Broken pipe


In [54]:
print("Top 5 rows from s3://{}/{}/train/".format(bucket, input_preprocessed_prefix_flights))
!aws s3 cp --quiet s3://$bucket/$input_preprocessed_prefix_flights/train/part-00000-1853362b-e8c2-4087-b5b4-30c05b6e59df-c000.csv - | head -n5

Top 5 rows from s3://sagemaker-us-east-1-193890026231/sagemaker/spark-preprocess-flights/2021-12-06-04-53-28/input/preprocessed/flights/train/
0.0,2016-01-01T08:10:00Z,NA,2016-01-01T09:04:00Z,NA,Cancelado,AUTORIZADO,40.0,97.0
0.0,2016-01-01T08:10:00Z,NA,2016-01-01T09:04:00Z,NA,Cancelado,AUTORIZADO,40.0,97.0
0.0,2016-01-01T08:10:00Z,NA,2016-01-01T09:04:00Z,NA,Cancelado,AUTORIZADO,40.0,97.0
0.0,2016-01-01T08:10:00Z,NA,2016-01-01T09:04:00Z,NA,Cancelado,AUTORIZADO,40.0,97.0
0.0,2016-01-01T09:38:00Z,2016-01-01T09:38:00Z,2016-01-01T11:13:00Z,2016-01-01T11:13:00Z,Realizado,NA,97.0,82.0


In [50]:
!aws s3 ls s3://$bucket/$input_preprocessed_prefix_flights/validation/ | head -n5

2021-12-06 04:59:52          0 _SUCCESS
2021-12-06 04:59:48   16074952 part-00000-0cad1ddb-5d15-47d7-93ae-22ae394f4313-c000.csv
2021-12-06 04:59:49   16076969 part-00001-0cad1ddb-5d15-47d7-93ae-22ae394f4313-c000.csv
2021-12-06 04:59:48   16121599 part-00002-0cad1ddb-5d15-47d7-93ae-22ae394f4313-c000.csv
2021-12-06 04:59:48   16049750 part-00003-0cad1ddb-5d15-47d7-93ae-22ae394f4313-c000.csv

[Errno 32] Broken pipe
Exception ignored in: <_io.TextIOWrapper name='<stdout>' mode='w' encoding='UTF-8'>
BrokenPipeError: [Errno 32] Broken pipe


In [51]:
!aws s3 ls s3://$bucket/$input_preprocessed_prefix_flights/airport/ | head -n5

2021-12-06 04:59:59          0 _SUCCESS
2021-12-06 04:59:55       1012 part-00000-2fa39bed-385f-41b2-ac79-7360353e08ed-c000.csv
2021-12-06 04:59:55        920 part-00001-2fa39bed-385f-41b2-ac79-7360353e08ed-c000.csv
2021-12-06 04:59:55        860 part-00002-2fa39bed-385f-41b2-ac79-7360353e08ed-c000.csv
2021-12-06 04:59:55        898 part-00003-2fa39bed-385f-41b2-ac79-7360353e08ed-c000.csv

[Errno 32] Broken pipe
Exception ignored in: <_io.TextIOWrapper name='<stdout>' mode='w' encoding='UTF-8'>
BrokenPipeError: [Errno 32] Broken pipe


In [55]:
print("Top 5 rows from s3://{}/{}/train/".format(bucket, input_preprocessed_prefix_flights))
!aws s3 cp --quiet s3://$bucket/$input_preprocessed_prefix_flights/airport/part-00000-2fa39bed-385f-41b2-ac79-7360353e08ed-c000.csv - | head -n5

Top 5 rows from s3://sagemaker-us-east-1-193890026231/sagemaker/spark-preprocess-flights/2021-12-06-04-53-28/input/preprocessed/flights/train/
Buenos Aires/Aeroparque,N/I,Buenos Aires/Aeroparque,Argentina,-58.536759,-34.816662
Professor Eriberto Manoel Reino,SP,Sao Jose Do Rio Preto,Brasil,-49.4066209,-20.8159034
Aeroporto De Jaguaruna,SC,Jaguaruna,Brasil,-49.0663451,-28.6767653
Fort Lauderdale,N/I,Fort Lauderdale,Estados Unidos,-80.1506022,26.0742344
Professor Urbano Ernesto Stumpf,SP,Sao Jose Dos Campos,Brasil,-45.8620445,-23.2256787


In [52]:
!aws s3 ls s3://$bucket/$input_preprocessed_prefix_flights/flights/ | head -n5

2021-12-06 05:00:07          0 _SUCCESS
2021-12-06 05:00:01      11782 part-00000-fedfac6c-2be0-4103-b09a-f39745727df9-c000.csv
2021-12-06 05:00:01      12385 part-00001-fedfac6c-2be0-4103-b09a-f39745727df9-c000.csv
2021-12-06 05:00:01      11070 part-00002-fedfac6c-2be0-4103-b09a-f39745727df9-c000.csv
2021-12-06 05:00:01      11348 part-00003-fedfac6c-2be0-4103-b09a-f39745727df9-c000.csv

[Errno 32] Broken pipe
Exception ignored in: <_io.TextIOWrapper name='<stdout>' mode='w' encoding='UTF-8'>
BrokenPipeError: [Errno 32] Broken pipe


In [56]:
print("Top 5 rows from s3://{}/{}/train/".format(bucket, input_preprocessed_prefix_flights))
!aws s3 cp --quiet s3://$bucket/$input_preprocessed_prefix_flights/flights/part-00000-fedfac6c-2be0-4103-b09a-f39745727df9-c000.csv - | head -n5

Top 5 rows from s3://sagemaker-us-east-1-193890026231/sagemaker/spark-preprocess-flights/2021-12-06-04-53-28/input/preprocessed/flights/train/
2225.0,TAM - 3639,TAM,Nacional
1303.0,GLO - 1505,GOL,Nacional
1101.0,GLO - 1552,GOL,Nacional
86.0,GLO - 2125,GOL,Nacional
2264.0,GLO - 2166,GOL,Nacional


## 5 Exploratory Data Analysis

Here we will perform a symple EDA to get some insights about our dataset.

* What are the main routes in Brazil?
* Which airline operates more flights in Brazil?
* What are the busiest airports in Brazil?
* What are the main routes for each airport?
* Visualizing routes by airport:
* Visualizing routes by airline:
* What airline has more delayed flights:
* What are the most delayed routes?
* What are the most common reasons for delays?
* At what time and day of the week do delays happen the most?

In [ ]:
df_airports = pd.read_csv('./datasets/df_airports.csv', encoding="latin1")
df_flights = pd.read_csv('./datasets/df_flights.csv', encoding="latin1")
df_trips = pd.read_csv('./datasets/df_trips.csv', encoding="latin1")

In [ ]:
df_trips.head()

### 5.1 What are the main routes in Brazil?

In [ ]:
main_routes = df_trips.groupby(['airport_id_origin', 'airport_id_destination'], as_index=False)['flight_no']\
    .count()\
    .rename(columns={'flight_no':'total_flights'})\
    .sort_values('total_flights', ascending=False)\
    .merge(df_airports[['airport_id', 'airport']], left_on='airport_id_origin', right_on='airport_id', how='left')\
    .merge(df_airports[['airport_id', 'airport']], left_on='airport_id_destination', right_on='airport_id', how='left', suffixes=('_origin', '_destination'))\
    [['airport_origin','airport_destination', 'total_flights']]

main_routes['route'] = main_routes['airport_origin'].astype(str) + ' : ' + main_routes['airport_destination'].astype(str)
main_routes = main_routes[['route','total_flights']]

In [ ]:
plt.subplots(figsize=(6, 10))
sns.barplot(data=main_routes.head(20), x='total_flights', y='route')

So, from now on, the data to be used on EDA will be the Train dataset.

As a first step, it may be interesting to visualize how flights connects Brazilian and Foreign cities worldwide. An interesting approach is available at [coderzcolumn tutorials](https://coderzcolumn.com/tutorials/data-science/how-to-create-connection-map-chart-in-python-jupyter-notebook-plotly-and-geopandas#2.2).

In [ ]:
## Please make a note that we are only taking first 2k to make run easy.
## final notebook should not have this.
df_sample = df_train.sample(frac=1.0).head(2000)

#international flights only
df_int = df_sample[df_sample["route_type"] == 'Internacional']

#national flights only
df_nat = df_sample[df_sample["route_type"] == 'Nacional']

#national flights only
df_reg = df_sample[df_sample["route_type"] == 'Regional']

In [ ]:
df_int.head()

In [ ]:
df_nat.head()

In [ ]:
df_reg.head()

In [ ]:
#plotting international flights
df_cnt = df_int.groupby(["lon_dest","lat_dest","lon_orig","lat_orig"]).count()[["flight_no"]].rename(columns={"flight_no":"num_flights"}).reset_index()
df_cnt = df_cnt.merge(df_int, how="left", left_on=["lon_dest","lat_dest","lon_orig","lat_orig"], right_on=["lon_dest","lat_dest","lon_orig","lat_orig"])

df_cnt.head()

In [ ]:
import plotly.graph_objects as go

In [ ]:
fig = go.Figure()

source_to_dest = zip(df_cnt["lat_orig"], df_cnt["lat_dest"],
                     df_cnt["lon_orig"], df_cnt["lon_dest"],
                     df_cnt["num_flights"])

## Loop thorugh each flight entry to add line between source and destination
for slat,dlat, slon, dlon, num_flights in source_to_dest:
    fig.add_trace(go.Scattergeo(
                        lat = [slat,dlat],
                        lon = [slon, dlon],
                        mode = 'lines',
                        line = dict(width = num_flights/50, color="red")
                        ))

## Logic to create labels of source and destination cities of flights
cities = df_cnt["city_orig"].values.tolist()+df_cnt["city_dest"].values.tolist()
countries = df_cnt["country_orig"].values.tolist()+df_cnt["country_dest"].values.tolist()
scatter_hover_data = [country + " : "+ city for city, country in zip(cities, countries)]

## Loop thorugh each flight entry to plot source and destination as points.
fig.add_trace(
    go.Scattergeo(
                lon = df_cnt["lon_orig"].values.tolist()+df_cnt["lon_dest"].values.tolist(),
                lat = df_cnt["lat_orig"].values.tolist()+df_cnt["lat_dest"].values.tolist(),
                hoverinfo = 'text',
                text = scatter_hover_data,
                mode = 'markers',
                marker = dict(size = 10, color = 'blue', opacity=0.1))
    )

## Update graph layout to improve graph styling.
fig.update_layout(title_text="Connection Map Depicting Flights from Brazil to All Other Countries",
                  height=700, width=900,
                  margin={"t":0,"b":0,"l":0, "r":0, "pad":0},
                  showlegend=False,
                  geo= dict(showland = True, landcolor = 'white', countrycolor = 'grey', bgcolor="lightgrey"))

fig.show()

In [ ]:
#plotting national flights
df_cnt = df_nat.groupby(["lon_dest","lat_dest","lon_orig","lat_orig"]).count()[["flight_no"]].rename(columns={"flight_no":"num_flights"}).reset_index()
df_cnt = df_cnt.merge(df_nat, how="left", left_on=["lon_dest","lat_dest","lon_orig","lat_orig"], right_on=["lon_dest","lat_dest","lon_orig","lat_orig"])

df_cnt.head()

In [ ]:
fig = go.Figure()

source_to_dest = zip(df_cnt["lat_orig"], df_cnt["lat_dest"],
                     df_cnt["lon_orig"], df_cnt["lon_dest"],
                     df_cnt["num_flights"])

## Loop thorugh each flight entry to add line between source and destination
for slat,dlat, slon, dlon, num_flights in source_to_dest:
    fig.add_trace(go.Scattergeo(
                        lat = [slat,dlat],
                        lon = [slon, dlon],
                        mode = 'lines',
                        line = dict(width = num_flights/50, color="red")
                        ))

## Logic to create labels of source and destination cities of flights
cities = df_cnt["city_orig"].values.tolist()+df_cnt["city_dest"].values.tolist()
countries = df_cnt["country_orig"].values.tolist()+df_cnt["country_dest"].values.tolist()
scatter_hover_data = [country + " : "+ city for city, country in zip(cities, countries)]

## Loop thorugh each flight entry to plot source and destination as points.
fig.add_trace(
    go.Scattergeo(
                lon = df_cnt["lon_orig"].values.tolist()+df_cnt["lon_dest"].values.tolist(),
                lat = df_cnt["lat_orig"].values.tolist()+df_cnt["lat_dest"].values.tolist(),
                hoverinfo = 'text',
                text = scatter_hover_data,
                mode = 'markers',
                marker = dict(size = 5, color = 'blue', opacity=0.1))
    )

## Update graph layout to improve graph styling.
fig.update_layout(
                  height=500, width=800, margin={"t":0,"b":0,"l":0, "r":0, "pad":0},
                  showlegend=False,
                  title_text = 'Connection Map Depicting Flights between Cities of Brazil',
                  geo = dict(projection_type = 'natural earth',scope = 'south america'),
                )

fig.show()

In [ ]:
#plotting regional flights
df_cnt = df_reg.groupby(["lon_dest","lat_dest","lon_orig","lat_orig"]).count()[["flight_no"]].rename(columns={"flight_no":"num_flights"}).reset_index()
df_cnt = df_cnt.merge(df_reg, how="left", left_on=["lon_dest","lat_dest","lon_orig","lat_orig"], right_on=["lon_dest","lat_dest","lon_orig","lat_orig"])

df_cnt.head()

In [ ]:
fig = go.Figure()

source_to_dest = zip(df_cnt["lat_orig"], df_cnt["lat_dest"],
                     df_cnt["lon_orig"], df_cnt["lon_dest"],
                     df_cnt["num_flights"])

## Loop thorugh each flight entry to add line between source and destination
for slat,dlat, slon, dlon, num_flights in source_to_dest:
    fig.add_trace(go.Scattergeo(
                        lat = [slat,dlat],
                        lon = [slon, dlon],
                        mode = 'lines',
                        line = dict(width = num_flights/50, color="red")
                        ))

## Logic to create labels of source and destination cities of flights
cities = df_cnt["city_orig"].values.tolist()+df_cnt["city_dest"].values.tolist()
countries = df_cnt["country_orig"].values.tolist()+df_cnt["country_dest"].values.tolist()
scatter_hover_data = [country + " : "+ city for city, country in zip(cities, countries)]

## Loop thorugh each flight entry to plot source and destination as points.
fig.add_trace(
    go.Scattergeo(
                lon = df_cnt["lon_orig"].values.tolist()+df_cnt["lon_dest"].values.tolist(),
                lat = df_cnt["lat_orig"].values.tolist()+df_cnt["lat_dest"].values.tolist(),
                hoverinfo = 'text',
                text = scatter_hover_data,
                mode = 'markers',
                marker = dict(size = 5, color = 'blue', opacity=0.1))
    )

## Update graph layout to improve graph styling.
fig.update_layout(
                  height=500, width=800, margin={"t":0,"b":0,"l":0, "r":0, "pad":0},
                  showlegend=False,
                  title_text = 'Connection Map Depicting Flights between Cities of Brazil',
                  geo = dict(projection_type = 'natural earth',scope = 'south america'),
                )

fig.show()

As a next step on the EDA, a comparision of the # of flights by each type of route might be relevant. To perform the EDA, no need to use a sampled dataset derived from df_train.

In [ ]:
#international flights only
df_int = df_train[df_train["route_type"] == 'Internacional']

#national flights only
df_nat = df_train[df_train["route_type"] == 'Nacional']

#national flights only
df_reg = df_train[df_train["route_type"] == 'Regional']

In [ ]:
ax = sns.countplot(x="route_type", data=df_train)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Route type')
ax.set_ylabel('# of flights')
plt.show()

This seems to be an interesting information as there are expressively more 'Nacional' flights than 'Internacional' and 'Regional'. This sees to indicate that most of airline companies operates within a majority of 'Nacional' route types on its business model.
Going further, a check on companies share of flights seems relevant.

In [ ]:
airlines = df_train.airline_company.value_counts()
airlines = airlines[airlines > 0]
plt.figure(figsize=(15,6))
plot = airlines.plot(kind="bar")
plot.set_title("Biggest Airline Companies in Brazil")

It is noticiable that Tam, Azul and Gol are the biggest airline companies operating in Brazil.
Another approach is repear the comparision but checking only each route type separated.

In [ ]:
airlines = df_int.airline_company.value_counts()
airlines = airlines[airlines > 0]
plt.figure(figsize=(15,6))
plot = airlines.plot(kind="bar")
plot.set_title("Biggest International Operators in Brazil")

By looking into International slice of flights, it is noticiable that American Airlines is also a major player in Brazilian market for this route type.

In [ ]:
airlines = df_nat.airline_company.value_counts()
airlines = airlines[airlines > 0]
plt.figure(figsize=(15,6))
plot = airlines.plot(kind="bar")
plot.set_title("Biggest National Operators in Brazil")

By checking only 'National' flights, it pops out the great concentration on Brazilian market, that is dominated by only 4 companies in a total of 7 companies active in this market.

The same approach can be applied for 'Regional' flights.

In [ ]:
airlines = df_reg.airline_company.value_counts()
airlines = airlines[airlines > 0]
plt.figure(figsize=(15,6))
plot = airlines.plot(kind="bar")
plot.set_title("Biggest Regional Operators in Brazil")

Regional flights is even more restrict, with 6 active companies only. The same top 3 from National airlines are also leading this segment.

As a next step, it is also possible to explore a little deeper on this dataset by checking flights Canceled or Completed.

In [ ]:
ax = sns.countplot(x="route_type", hue="flight_status", data=df_train)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Route type')
ax.set_ylabel('# of flights')
plt.show()

Something that is noticiable is that the number of cancelled flights for 'Internacional' flights is expressively smaller than 'Nacional' flights. At least visually, it is also noticiable that a 'Regional' flight is more likely to be cancelled than a 'Nacional' flight, based on the bars comparision.

 It is also possible to dive in to check flight status within each type of route.

In [ ]:
ax = sns.countplot(x="airline_company", hue="flight_status", order = df_int['airline_company'].value_counts().head(20).index, data=df_int)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Flight status by each company')
ax.set_ylabel('# of flights')
plt.show()


Checking above comparision, some can say that Gol is an airline company to be avoided when talking about international flights. Its rate of cancelation is bigger than every other company. It seems to be some times bigger than Tam airline company. Air France(TAP)?? is also an airline company that is worth to be careful, although the flight number is small, the cancellation rate seems also expressive.

In [ ]:
ax = sns.countplot(x="airline_company", hue="flight_status", order = df_nat['airline_company'].value_counts().head(7).index, data=df_nat)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Flight status by each company')
ax.set_ylabel('# of flights')
plt.show()

Analyzing National data, Gol is also a company to avoid, as it has twice as many cancellation than Azul, which is the second in this list.

In [ ]:
ax = sns.countplot(x="airline_company", hue="flight_status", order = df_reg['airline_company'].value_counts().head(6).index, data=df_reg)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Flight status by each company')
ax.set_ylabel('# of flights')
plt.show()

On Regional flights, Azul is the company that is clearly to avoid as it has a cancellation rate so high that it is (almost the same number)?? of flights that were effectively done.

Another important information about flight is to known how likely a flight will happen but in a delayed time.
In order to do so, by checking Justification field is enough to determine if a flight was delayed or not. If this field is not 'NaN', it means that the flight was delayed. An anticipation of a new feature 'Delayed' comes in at this time.

In [ ]:
df_train['is_delayed'] = df_train['just_code'].str.len() > 0

#international flights only
df_int = df_train[df_train["route_type"] == 'Internacional']

#national flights only
df_nat = df_train[df_train["route_type"] == 'Nacional']

#national flights only
df_reg = df_train[df_train["route_type"] == 'Regional']

Also, a cancelled flight should not be considered in this analysis, so in each of the analysis below, cancelled flights will be removed from dataset.

In [ ]:
ax = sns.countplot(x="route_type", hue="is_delayed", data=df_train[df_train["flight_status"] == 'Realizado'])
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_xlabel('Route type')
ax.set_ylabel('# of flights')
ax.set_title('Delayed flights by Route type')
plt.show()

Aproximately 40% of national flights are delayed, which seems to be a huge number of flights. International flights are delayed in aproximately 20% of the flights and Regional flights are even less delayed, aproximately 10%, in a visual inspection of this plot.

In [ ]:
ds = df_int[df_int["flight_status"] == 'Realizado']

ax = sns.countplot(x="airline_company", hue="is_delayed", order = ds['airline_company'].value_counts().head(20).index, data=ds)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_title('Delayed flights by each Company - International')
ax.set_xlabel('Airline company')
ax.set_ylabel('# of flights')
plt.show()


In [ ]:
df_int['Departure_Delays'] =df_int.departure_actual - df_int.departure_schedule
#df_int['Departure_Delays'] = df_int['Departure_Delays'].apply(lambda x : round(x.total_seconds()/60)) sep ==Realizados

def get_stats(group):
    return {'min': group.min(), 'max': group.max(),
            'count': group.count(), 'mean': group.mean()}
#_______________________________________________________________
# Creation of a dataframe with statitical infos on each airline:
global_stats = df_int['Departure_Delays'].groupby(df_int['airline_company']).apply(get_stats).unstack()
global_stats = global_stats.sort_values(by = 'count', ascending=False)
global_stats.head(10)


In [ ]:
airport_stats = df_int['Departure_Delays'].groupby(df_int['airport_orig']).apply(get_stats).unstack()
airport_stats = airport_stats.sort_values(by = 'count', ascending=False)
airport_stats.head(10)

By analysing this data segregated by airline company for international flights, Azul(TAM?) is the company that has the higher proportion of delayed flights among its total. Delayed flights are twice as many of flights without delay for Azul company.

In [ ]:
ds = df_nat[df_nat["flight_status"] == 'Realizado']

ax = sns.countplot(x="airline_company", hue="is_delayed", order = ds['airline_company'].value_counts().head(7).index, data=ds)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_title('Delayed flights by each Company - National')
ax.set_xlabel('Airline company')
ax.set_ylabel('# of flights')
plt.show()


Considering only national flights, Azul is by far the worst company in terms of following the appointment. Delayed flights sum more than 5 times of the flights that are in time.

In [ ]:
ds = df_reg[df_reg["flight_status"] == 'Realizado']

ax = sns.countplot(x="airline_company", hue="is_delayed", order = ds['airline_company'].value_counts().head(6).index, data=ds)
plt.xticks(rotation=90)
mticker = ticker.ScalarFormatter(useOffset=False)
ax = plt.gca()
ax.yaxis.set_major_formatter(mticker)
ax.ticklabel_format(axis='y', style='plain', useOffset=False)
ax.set_title('Delayed flights by each Company - Regional')
ax.set_xlabel('Airline company')
ax.set_ylabel('# of flights')
plt.show()

Taking into account only the Regional flights, it seems pretty much clear that Azul has a very good performance in terms of being on time for this category of flight. Gol is also another Regional operator which stands for pontuality.

In [ ]:
print(df_train['departure_actual'].dt.year.value_counts().sort_index())

Per year, in the base there are: 3 flights in 2014, 611514 flights in 2015, 542521 flights in 2016 and 310,560 flights in 2017. We can see the distribution of these numbers in a bar chart.

In [ ]:
df_train.groupby(df_train['departure_actual'].dt.year).count()['flight_no'].plot.barh()

Airports most used as origin of flights.

In [ ]:
plt.figure(figsize=(10,6))
plot = df_train.airport_orig.value_counts().head(10).plot(kind="bar")
plot.set_title("Top 10 origin airports.")

These airports belong to the cities:

In [ ]:
plt.figure(figsize=(10,6))
plot = df_train.city_orig.value_counts().head(10).plot(kind="bar")
plot.set_title("Top origin cities")

## 6 Machine Learning algorithms

In [ ]:
df_trips.columns

In [ ]:
df_flights.columns

In [ ]:
# model = df_full\
#     .drop(df_full.query('flight_status == "Cancelado"').index)\
#     .drop(columns=['flight_status','arrival_schedule','arrival_actual','just_code', 'lon_dest', 'lat_dest', 'lon_orig', 'lat_orig'])
model = df_trips\
    .drop(df_trips[df_trips['flight_status'] == "Cancelado"].index)\
    .drop(columns=['flight_status','arrival_schedule','arrival_actual','just_code'])\
    .merge(df_flights, on='flight_no', how='left')\
    .drop(columns='route_type')
model['departure_delay'] = (model['departure_actual'] - model['departure_schedule']).dt.total_seconds()
model.info()

In [ ]:
model.isnull().sum()

### 6.1 Creating the train and test datasets

In [ ]:
from sklearn.model_selection import train_test_split
#keep 35% os test data seems interesting, given the fact that a huge dataset is available.
testsize = 0.35

#random seed fixed as 42, in order to keep reproducibility.
randomseed = 42

df_train, df_test = train_test_split(model, test_size=testsize, random_state=randomseed)

### 6.2 Creating new info

In [ ]:
# create new columns
df_train['schedule_day'] = df_train['departure_schedule'].dt.day
df_train['schedule_month'] = df_train['departure_schedule'].dt.month
df_train['schedule_year'] = df_train['departure_schedule'].dt.year
df_train['schedule_time'] = df_train['departure_schedule'].dt.hour.astype(int) * 100 + np.where(df_train['departure_schedule'].dt.minute.astype(int) < 30, 0, 30)
df_train['schedule_weekday'] = df_train['departure_schedule'].dt.weekday
df_train.head(2)

In [ ]:
df_train['flight_delay'] = df_train.groupby('flight_no')['departure_delay'].transform('mean')
df_train['flight_day_delay'] = df_train.groupby(['flight_no','schedule_day'])['departure_delay'].transform('mean')
df_train['flight_month_delay'] = df_train.groupby(['flight_no','schedule_month'])['departure_delay'].transform('mean')
df_train['flight_year_delay'] = df_train.groupby(['flight_no','schedule_year'])['departure_delay'].transform('mean')
df_train['flight_time_delay'] = df_train.groupby(['flight_no','schedule_time'])['departure_delay'].transform('mean')
df_train['flight_weekday_delay'] = df_train.groupby(['flight_no','schedule_weekday'])['departure_delay'].transform('mean')
df_train['airline_delay'] = df_train.groupby('airline_company')['departure_delay'].transform('mean')
df_train['airline_day_delay'] = df_train.groupby(['airline_company','schedule_day'])['departure_delay'].transform('mean')
df_train['airline_month_delay'] = df_train.groupby(['airline_company','schedule_month'])['departure_delay'].transform('mean')
df_train['airline_year_delay'] = df_train.groupby(['airline_company','schedule_year'])['departure_delay'].transform('mean')
df_train['airline_time_delay'] = df_train.groupby(['airline_company','schedule_time'])['departure_delay'].transform('mean')
df_train['airline_weekday_delay'] = df_train.groupby(['airline_company','schedule_weekday'])['departure_delay'].transform('mean')

df_train['flight_delay_median'] = df_train.groupby('flight_no')['departure_delay'].transform('median')
df_train['flight_day_delay_median'] = df_train.groupby(['flight_no','schedule_day'])['departure_delay'].transform('median')
df_train['flight_month_delay_median'] = df_train.groupby(['flight_no','schedule_month'])['departure_delay'].transform('median')
df_train['flight_year_delay_median'] = df_train.groupby(['flight_no','schedule_year'])['departure_delay'].transform('median')
df_train['flight_time_delay_median'] = df_train.groupby(['flight_no','schedule_time'])['departure_delay'].transform('median')
df_train['flight_weekday_delay_median'] = df_train.groupby(['flight_no','schedule_weekday'])['departure_delay'].transform('median')
df_train['airline_delay_median'] = df_train.groupby('airline_company')['departure_delay'].transform('median')
df_train['airline_day_delay_median'] = df_train.groupby(['airline_company','schedule_day'])['departure_delay'].transform('median')
df_train['airline_month_delay_median'] = df_train.groupby(['airline_company','schedule_month'])['departure_delay'].transform('median')
df_train['airline_year_delay_median'] = df_train.groupby(['airline_company','schedule_year'])['departure_delay'].transform('median')
df_train['airline_time_delay_median'] = df_train.groupby(['airline_company','schedule_time'])['departure_delay'].transform('median')
df_train['airline_weekday_delay_median'] = df_train.groupby(['airline_company','schedule_weekday'])['departure_delay'].transform('median')

In [ ]:
df_train.head()

In [ ]:
df_train.corr()['departure_delay'].sort_values()

In [ ]:
df_train.columns

In [ ]:
df_train_clean = df_train.drop(columns=[
       'flight_no', 'departure_schedule', 'departure_actual',
       'airport_id_origin', 'airport_id_destination', 'airline_company',
       'schedule_day', 'schedule_month', 'schedule_year',
       'schedule_time', 'schedule_weekday',])
df_train_clean.head()

In [ ]:
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.compose import make_column_transformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.impute import SimpleImputer

numerical_pipeline = make_pipeline(SimpleImputer(), StandardScaler())
categorical_pipeline = make_pipeline(SimpleImputer(strategy='most_frequent'), OneHotEncoder(handle_unknown = "ignore"))

preprocessor = make_column_transformer((numerical_pipeline, numerical_features), 
                                       (categorical_pipeline, categorical_features))

In [ ]:
X_tr = df_train.drop('late', axis=1)
y_tr = df_train['late']

X_tr = X_tr.sample(n=10000)
y_tr = y_tr.sample(n=10000)

In [ ]:
X_tes = df_test.drop('late', axis=1)
y_tes = df_test['late']

y_tes = y_tes.sample(n=10000)
y_tes = y_tes.sample(n=10000)

### Model selection

In [ ]:
from sklearn.model_selection import cross_validate

def crossVal_model(preprocessor, estimator, X_tr, y_tr):
    
    #model
    model = make_pipeline(preprocessor, estimator)
    
    #cross validation
    scr = cross_validate(model, X_tr, y_tr, cv=5, scoring=['f1', 'precision', 'recall'])
    
    #metrics
    print("reacall = {:.0%}".format(scr['test_recall'].mean()))
    print("precision = {:.0%}".format(scr['test_precision'].mean()))
    print("f1 = {:.0%}".format(scr['test_f1'].mean()))
    
    return model, scr


### Tree

In [ ]:
from sklearn.tree import DecisionTreeClassifier

estimator = DecisionTreeClassifier()
m_tree = crossVal_model(preprocessor, estimator, X_tr, y_tr)

### Stochastic Gradient Descent

In [ ]:
from sklearn.linear_model import SGDClassifier

estimator = SGDClassifier()
m_sgdc = crossVal_model(preprocessor, estimator, X_tr, y_tr)


### K nearest neighbors

In [ ]:
from sklearn.neighbors import KNeighborsClassifier

estimator = KNeighborsClassifier()
m_kn = crossVal_model(preprocessor, estimator, X_tr, y_tr)


### Linear SVC

In [ ]:
from sklearn.svm import LinearSVC

estimator = LinearSVC()
m_svc = crossVal_model(preprocessor, estimator, X_tr, y_tr)

### Test

In [ ]:
from sklearn.metrics import plot_confusion_matrix, precision_score, recall_score, f1_score

model = m_tree[0]
model.fit(X_tr, y_tr)
y_pred = model.predict(X_tes)
plot_confusion_matrix(model, X_tes, y_tes);

p = precision_score(y_tes, y_pred)
r = recall_score(y_tes, y_pred)
f1 = f1_score(y_tes, y_pred)

print('recall = {:.0%}'.format(r))
print('precision = {:.0%}'.format(p))
print('f1 = {:.0%}'.format(f1))

In [ ]:
y_pred[100:120]

In [ ]:
np.array(y_tes[100:120])